In [1]:
!pip install langchain_openai
!pip install langchain-community
!pip install pypdf
!pip install faiss-cpu

  Using cached pypdf-5.3.1-py3-none-any.whl.metadata (7.3 kB)
Using cached pypdf-5.3.1-py3-none-any.whl (302 kB)


In [9]:
from dotenv import load_dotenv
import os

load_dotenv()  # .env 파일에서 환경 변수 로드
os.environ["OPENAI_API_KEY"] = os.getenv("OPENAI_API_KEY")  # OPENAI_API_KEY 환경 변수 설정

In [7]:
from pathlib import Path
import pickle
import time
from tqdm import tqdm
from langchain_community.vectorstores import FAISS
from langchain_community.document_loaders import TextLoader
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain_openai import OpenAIEmbeddings, ChatOpenAI
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.documents import Document

####################
####### 데이터 준비 및 저장
###################

def process_text_by_lines():
    print("텍스트 파일 행별 처리 중...")
    with open("crawl/blog_contents_20250306.txt", 'r', encoding='utf-8') as file:
        lines = file.readlines()
    
    # 빈 줄 제거하고 각 행을 Document 객체로 변환
    documents = []
    for i, line in enumerate(lines):
        line = line.strip()
        if line:  # 빈 줄이 아닌 경우만 처리
            doc = Document(
                page_content=line,
                metadata={"line_number": i, "source": "blog_contents_20250306.txt"}
            )
            documents.append(doc)
    
    return documents

def save_data():
    print("데이터 저장 프로세스 시작...")
    total_start = time.time()
    
    # db 디렉토리 생성
    Path("db").mkdir(exist_ok=True)
    
    # 1. 문서 행별 로드 및 저장
    print("\n1. 문서 행별 로드 중...")
    start = time.time()
    docs = process_text_by_lines()
    with open("db/documents.pkl", "wb") as f:
        pickle.dump(docs, f)
    print(f"   전체 행 수: {len(docs)}개")
    print(f"   소요시간: {time.time() - start:.2f}초")
    
    # 2. 각 행별 청킹 및 저장
    print("\n2. 행별 청킹 중...")
    start = time.time()
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=1000,
        chunk_overlap=200,
        length_function=len,
        is_separator_regex=False
    )
    
    splits = []
    for doc in tqdm(docs, desc="   행별 청킹 진행률"):
        # 긴 행은 더 작은 청크로 분할
        if len(doc.page_content) > 1000:
            chunks = text_splitter.split_documents([doc])
            splits.extend(chunks)
        else:
            # 짧은 행은 그대로 유지
            splits.append(doc)
    
    with open("db/splits.pkl", "wb") as f:
        pickle.dump(splits, f)
    print(f"   최종 청크 수: {len(splits)}개")
    print(f"   소요시간: {time.time() - start:.2f}초")
    
    # 3. 벡터스토어 생성 및 저장
    print("\n3. 벡터스토어 생성 중...")
    start = time.time()
    embeddings = OpenAIEmbeddings(model="text-embedding-ada-002")
    
    # 청크를 100개씩 나누어 임베딩 진행
    batch_size = 100
    vectorstore = None
    
    for i in tqdm(range(0, len(splits), batch_size), desc="   임베딩 진행률"):
        batch = splits[i:i + batch_size]
        if vectorstore is None:
            vectorstore = FAISS.from_documents(documents=batch, embedding=embeddings)
        else:
            vectorstore.add_documents(batch)
    
    vectorstore.save_local("db/vectorstore")
    print(f"   소요시간: {time.time() - start:.2f}초")
    
    print(f"\n전체 프로세스 완료! 총 소요시간: {time.time() - total_start:.2f}초")
    return docs, splits, vectorstore

save_data()



데이터 저장 프로세스 시작...

1. 문서 행별 로드 중...
텍스트 파일 행별 처리 중...
   전체 행 수: 5624개
   소요시간: 0.17초

2. 행별 청킹 중...


   행별 청킹 진행률: 100%|██████████| 5624/5624 [00:01<00:00, 3469.71it/s]


   최종 청크 수: 17032개
   소요시간: 1.71초

3. 벡터스토어 생성 중...


   임베딩 진행률: 100%|██████████| 171/171 [14:44<00:00,  5.17s/it]


   소요시간: 884.75초

전체 프로세스 완료! 총 소요시간: 886.63초


([Document(metadata={'line_number': 0, 'source': 'blog_contents_20250306.txt'}, page_content='https://blog.naver.com/seulk29/223764907792\t\u200b\t사당역에서 만나기로 한 친구가 알아낸\t사당역 신상 맛집 사당룸 한식주점하제!\t새로 생긴지 얼마 되지 않은 술집이라\t아직 후기가 많지 않아 꼭!! 다녀온 후기를\t남겨야겠다고 마음먹은 곳 ㅎㅎ\t이런 장소를 알아낸 내 친구~ 칭찬해~\tㅋㅋㅋㅋㅋㅋ\t\u200b\t사당룸 한식주점 하제 후기 고고~~\t\u200b\t사당룸 한식주점하제\t\u200b\t📍 위치 : 서울 서초구 방배천로2길 21 6층\t⏰ 영업시간\t월 ~ 토 : 15시 ~ 25시\t(12시 라스트 오더)\t일 : 15시 ~ 24시\t(23시 라스트 오더)\t\u200b\t도착하자마자 예약자 명단에 이름이\t가득한 걸 보아하니 미리 예약을 해두고\t방문하는 것이 좋을 것 같다는 생각을 했다.\t우리도 사전에 미리 예약을 해둬 바로 입장할 수 있었음\t\u200b\t예약은 네이버 플레이스를 통해 가능하며,\t2인부터 7~8인 룸을 이용할 수 있다.\t\u200b\t위치\t사당역 13번 출구에서 도보로 3분 거리에 위치해 있다.\t\u200b\t사당룸 한식주점하제\t서울특별시 서초구 방배천로2길 21 6층\t이 블로그의 체크인\t이 장소의 다른 글\t\u200b\t외관\t\u200b\t이 건물의 6층에 위치해 있는 하제!\t\u200b\t\u200b\t엘리베이터를 타고 6층으로 올라간다. ㅎㅎ\t\u200b\t\u200b\t매장 내부\t\u200b\t6층에 내리면 바로 사당 룸한식주점 하제로 연결된다.\t층 전체를 단독으로 사용하고 있음!\t입구에서부터 분위기가 좋은 술집임이 느껴졌다.\t\u200b\t\u200b\t오~\t모든 좌석이 룸으로 프라이빗하게 구성되어 있다.\t복도에서부터 고급스러움이 느껴짐!\t\u200b\t\u200b\t문

In [24]:
####################
####### 저장된 데이터 로드
###################

def load_data():
    start = time.time()
    embeddings = OpenAIEmbeddings(model="text-embedding-ada-002")
    
    # documents.pkl로 파일명 수정
    with open("db/documents.pkl", "rb") as f:
        docs = pickle.load(f)
    with open("db/splits.pkl", "rb") as f:
        splits = pickle.load(f)
    vectorstore = FAISS.load_local("db/vectorstore", embeddings, allow_dangerous_deserialization=True)
    
    print(f"데이터 로드 완료! 소요시간: {time.time() - start:.2f}초")
    return docs, splits, vectorstore

####################
####### RAG 챗봇 구축
###################

def setup_rag():
    # 1. 저장된 데이터 로드
    docs, splits, vectorstore = load_data()
    
    # 2. LLM 모델 설정
    llm = ChatOpenAI(model="gpt-4o-mini")
    
    # 3. retriever 설정
    retriever = vectorstore.as_retriever(search_kwargs={"k": 3})  # 상위 3개 문서 검색
    
    # 4. 프롬프트 템플릿 설정
    prompt = ChatPromptTemplate.from_template("""
    오로지 아래의 context만을 기반으로 질문에 대답하세요:
    {context}
    질문:
    {question}
    """)
    
    # 5. Chain 구성
    def format_docs(docs):
        return "\n\n".join(doc.page_content for doc in docs)
    
    # 검색 결과를 저장할 전역 변수
    global last_retrieved_docs
    last_retrieved_docs = []
    
    def retrieve_and_store(query):
        global last_retrieved_docs
        docs = retriever.get_relevant_documents(query)
        last_retrieved_docs = docs
        return format_docs(docs)
    
    rag_chain = (
        {"context": lambda x: retrieve_and_store(x), "question": RunnablePassthrough()}
        | prompt
        | llm
        | StrOutputParser()
    )
    
    return rag_chain

####################
####### 실행
###################

def print_retrieved_docs():
    print("\n=== 검색된 관련 문서 ===")
    for i, doc in enumerate(last_retrieved_docs, 1):
        print(f"\n문서 {i}:")
        print(f"내용: {doc.page_content}")
        print(f"메타데이터: {doc.metadata}")

if __name__ == "__main__":
    # 최초 실행 시 데이터 저장
    # save_data()
    
    # RAG 챗봇 설정
    rag_chain = setup_rag()
    
    # 챗봇 실행
    query = "강남구 전시 추천해봐"
    start = time.time()
    
    # 응답 생성
    response = rag_chain.invoke(query)
    
    # 검색 결과 출력
    print_retrieved_docs()
    
    print(f"\n응답 생성 시간: {time.time() - start:.2f}초")
    print("\n=== AI 답변 ===")
    print(response)

데이터 로드 완료! 소요시간: 8.43초

=== 검색된 관련 문서 ===

문서 1:
내용: 이곳을 꼭 방문해보길 추천합니다다.	​	운동을 통해 얻는 성취감과 함께, 새로운 사람들과의 만남과 소통을 통해 더욱 풍성한 경험을 할 수 있을 것이라 생각됩니다.	​	이상, 강남 이색체험 손상원클라이밍짐 강남역점 후기를 마치겠습니다 :)	​	​	​	다음에는 어디로 가볼까요~? :)	손상원 클라이밍짐 강남역점	서울특별시 서초구 강남대로 331 지하1층	이 블로그의 체크인	이 장소의 다른 글	​
메타데이터: {'line_number': 2262, 'source': 'blog_contents_20250306.txt'}

문서 2:
내용: 즐길 수 있는 강남역 횟집 제철 회가 꽤 괜찮으니까 강남역에서 회가 먹고 싶다면 강남 자매수산 기억하시길 추천합니다~	주소: 서울 강남구 봉은사로 18길 90	헬로씨네	전화: 0507-1309-5534	영업시간: 14시~24시 / 라스트오더 23시	자매수산	서울특별시 강남구 봉은사로18길 90	강남역 2호선	서울특별시 강남구 강남대로 396	이 블로그의 체크인	#강남횟집	#강남역횟집	#강남가성비횟집	#강남역가성비횟집	#자매수산	#강남자매수산	​	이 포스팅은 업체에서 서비스를 제공받아 직접 체험 후 솔직하게 작성했습니다. by 헬씨네	​
메타데이터: {'line_number': 4325, 'source': 'blog_contents_20250306.txt'}

문서 3:
내용: 강남점 추천드립니다!	​	​	​	​	장인닭갈비 강남점 방문 정보	장인닭갈비 강남점	서울특별시 강남구 테헤란로1길 19	이 블로그의 체크인	이 장소의 다른 글	📍 서울 강남구 테헤란로1길 19	🕛 영업시간: 매일 11:00 - 24:00	🚆 강남역 11번 출구에서 도보 1분 거리	🚗 주차: 하이파킹 강남K스퀘어점 (30분 3,000원, 시간당 6,000원)	​	#닭갈비맛집	#강남역닭갈비	#강남역맛집	#장인닭갈비	#강남닭갈비	#강남역술집	#강남역한식	#강남역회식	#강남데

In [ ]:
from pathlib import Path
import pickle
from langchain_community.vectorstores import FAISS
from langchain_community.document_loaders import TextLoader
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain_openai import OpenAIEmbeddings, ChatOpenAI
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_core.prompts import ChatPromptTemplate
import time
from rank_bm25 import BM25Okapi
import numpy as np
from typing import List, Dict
import re

####################
####### 데이터 준비 및 저장
###################

####################
####### 저장된 데이터 로드
###################

def load_data():
    start = time.time()
    embeddings = OpenAIEmbeddings(model="text-embedding-ada-002")
    
    with open("db/documents.pkl", "rb") as f:
        docs = pickle.load(f)
    with open("db/splits.pkl", "rb") as f:
        splits = pickle.load(f)
    vectorstore = FAISS.load_local("db/vectorstore", embeddings, allow_dangerous_deserialization=True)
    
    print(f"데이터 로드 완료! 소요시간: {time.time() - start:.2f}초")
    return docs, splits, vectorstore

####################
####### 하이브리드 검색을 위한 클래스 추가
###################
class HybridRetriever:
    def __init__(self, vectorstore, splits, k: int = 3):
        self.vectorstore = vectorstore
        self.k = k
        
        # BM25 초기화
        # 텍스트 전처리
        tokenized_corpus = [self._tokenize(doc.page_content) for doc in splits]
        self.bm25 = BM25Okapi(tokenized_corpus)
        self.splits = splits
        
        # 서울시 구 리스트
        self.districts = [
            '종로구', '중구', '용산구', '성동구', '광진구', '동대문구', '중랑구', '성북구',
            '강북구', '도봉구', '노원구', '은평구', '서대문구', '마포구', '양천구', '강서구',
            '구로구', '금천구', '영등포구', '동작구', '관악구', '서초구', '강남구', '송파구', '강동구'
        ]
    
    def _tokenize(self, text: str) -> List[str]:
        # 간단한 토큰화 (공백 기준)
        return re.sub(r'[^\w\s]', '', text.lower()).split()
    
    def _extract_district(self, query: str) -> str:
        # 쿼리에서 구 이름 추출
        for district in self.districts:
            if district in query:
                return district
        return None
    
    def get_relevant_documents(self, query: str):
        print("\n=== 검색 프로세스 시작 ===")
        print(f"입력 쿼리: {query}")
        
        # 1. 쿼리에서 구 이름 추출
        district = self._extract_district(query)
        
        if district:
            print(f"\n1. 구 이름 추출: '{district}' 발견")
            
            # 2. BM25로 키워드 검색 (상위 10개)
            print("\n2. BM25 키워드 검색 수행 중...")
            tokenized_query = self._tokenize(district)
            bm25_scores = self.bm25.get_scores(tokenized_query)
            top_k_bm25 = np.argsort(bm25_scores)[-10:][::-1]
            
            # 3. BM25로 찾은 문서들에 대해서만 벡터 검색 수행
            filtered_docs = [self.splits[i] for i in top_k_bm25]
            print(f"   - BM25로 {len(filtered_docs)}개 문서 필터링됨")
            
            # 벡터스토어에서 필터링된 문서들만 검색 (원래 쿼리로 검색)
            print("\n3. 필터링된 문서에 대해 벡터 검색 수행 중...")
            # 먼저 벡터 검색 수행
            all_results = self.vectorstore.similarity_search(
                query,
                k=len(filtered_docs)  # 필터링된 문서 수만큼 검색
            )
            print(f"   - 벡터 검색으로 {len(all_results)}개 문서 검색됨")
            
            # 필터링된 문서와 일치하는 결과만 선택
            filtered_contents = set(doc.page_content for doc in filtered_docs)
            vector_results = [
                doc for doc in all_results 
                if doc.page_content in filtered_contents
            ][:self.k]
            print(f"   - BM25 필터링과 매칭된 문서: {len(vector_results)}개")
            
            # 결과가 k개 미만이면 일반 벡터 검색 결과로 보충
            if len(vector_results) < self.k:
                print(f"\n4. 결과 보충: 추가 {self.k - len(vector_results)}개 문서 검색 중...")
                additional_results = self.vectorstore.similarity_search(
                    query,
                    k=self.k - len(vector_results)
                )
                vector_results.extend(additional_results)
                print(f"   - 최종 검색 결과: {len(vector_results)}개 문서")
        else:
            print("\n1. 구 이름 없음 - 일반 벡터 검색 수행")
            # 구 이름이 없는 경우 일반 벡터 검색
            vector_results = self.vectorstore.similarity_search(
                query,
                k=self.k
            )
            print(f"   - 벡터 검색으로 {len(vector_results)}개 문서 검색됨")
        
        print("\n=== 검색 프로세스 완료 ===")
        return vector_results

####################
####### RAG 챗봇 구축
###################

def setup_rag():
    # 1. 저장된 데이터 로드
    docs, splits, vectorstore = load_data()
    
    # 2. LLM 모델 설정
    llm = ChatOpenAI(model="gpt-4o-mini")
    
    # 3. 하이브리드 retriever 설정
    retriever = HybridRetriever(vectorstore, splits, k=3)
    
    # 4. 프롬프트 템플릿 설정
    prompt = ChatPromptTemplate.from_template("""
    오로지 아래의 context만을 기반으로 질문에 대답하세요:
    {context}
    질문:
    {question}
    """)
    
    # 5. Chain 구성
    def format_docs(docs):
        return "\n\n".join(doc.page_content for doc in docs)
    
    # 검색 결과를 저장할 전역 변수
    global last_retrieved_docs
    last_retrieved_docs = []
    
    def retrieve_and_store(query):
        global last_retrieved_docs
        docs = retriever.get_relevant_documents(query)
        last_retrieved_docs = docs
        return format_docs(docs)
    
    rag_chain = (
        {"context": lambda x: retrieve_and_store(x), "question": RunnablePassthrough()}
        | prompt
        | llm
        | StrOutputParser()
    )
    
    return rag_chain

####################
####### 실행
###################

def print_retrieved_docs():
    print("\n=== 검색된 관련 문서 ===")
    for i, doc in enumerate(last_retrieved_docs, 1):
        print(f"\n문서 {i}:")
        print(f"내용: {doc.page_content}")
        print(f"메타데이터: {doc.metadata}")

if __name__ == "__main__":
    # 최초 실행 시 데이터 저장
    # save_data()
    
    # RAG 챗봇 설정
    rag_chain = setup_rag()
    
    # 챗봇 실행
    query = "강남구 전시 추천해줘"
    start = time.time()
    
    # 응답 생성
    response = rag_chain.invoke(query)
    
    # 검색 결과 출력
    print_retrieved_docs()
    
    print(f"\n응답 생성 시간: {time.time() - start:.2f}초")
    print("\n=== AI 답변 ===")
    print(response)

데이터 로드 완료! 소요시간: 0.66초

=== 검색 프로세스 시작 ===
입력 쿼리: 강남구 전시 추천해줘

1. 구 이름 추출: '강남구' 발견

2. BM25 키워드 검색 수행 중...
   - BM25로 10000개 문서 필터링됨

3. 필터링된 문서에 대해 벡터 검색 수행 중...
   - 벡터 검색으로 10000개 문서 검색됨
   - BM25 필터링과 매칭된 문서: 3개

=== 검색 프로세스 완료 ===

=== 검색된 관련 문서 ===

문서 1:
내용: 이곳을 꼭 방문해보길 추천합니다다.	​	운동을 통해 얻는 성취감과 함께, 새로운 사람들과의 만남과 소통을 통해 더욱 풍성한 경험을 할 수 있을 것이라 생각됩니다.	​	이상, 강남 이색체험 손상원클라이밍짐 강남역점 후기를 마치겠습니다 :)	​	​	​	다음에는 어디로 가볼까요~? :)	손상원 클라이밍짐 강남역점	서울특별시 서초구 강남대로 331 지하1층	이 블로그의 체크인	이 장소의 다른 글	​
메타데이터: {'line_number': 2262, 'source': 'blog_contents_20250306.txt'}

문서 2:
내용: 즐길 수 있는 강남역 횟집 제철 회가 꽤 괜찮으니까 강남역에서 회가 먹고 싶다면 강남 자매수산 기억하시길 추천합니다~	주소: 서울 강남구 봉은사로 18길 90	헬로씨네	전화: 0507-1309-5534	영업시간: 14시~24시 / 라스트오더 23시	자매수산	서울특별시 강남구 봉은사로18길 90	강남역 2호선	서울특별시 강남구 강남대로 396	이 블로그의 체크인	#강남횟집	#강남역횟집	#강남가성비횟집	#강남역가성비횟집	#자매수산	#강남자매수산	​	이 포스팅은 업체에서 서비스를 제공받아 직접 체험 후 솔직하게 작성했습니다. by 헬씨네	​
메타데이터: {'line_number': 4325, 'source': 'blog_contents_20250306.txt'}

문서 3:
내용: 강남점 추천드립니다!	​	​	​	​	장인닭갈비 강남점 방문 정보	장인닭갈비 강남점	서울특